In [1]:
import random
from datetime import datetime

import numpy as np
import pandas as pd
import torch
from torch import nn, optim
from torch.utils.data import DataLoader
from torch.utils.data import TensorDataset
from tqdm import tqdm

In [2]:
torch.backends.cudnn.deterministic = True
torch.backends.cudnn.benchmark = False

DEVICE = 'cuda:0' if torch.cuda.is_available() else 'cpu'

In [3]:
train_data = pd.read_csv('./data/train.csv').drop([379, 24598], axis=0)
test_data = pd.read_csv('./data/test_x.csv')
# drop_list = ['QaE', 'QbE', 'QcE', 'QdE', 'QeE',
#              'QfE', 'QgE', 'QhE', 'QiE', 'QjE',
#              'QkE', 'QlE', 'QmE', 'QnE', 'QoE',
#              'QpE', 'QqE', 'QrE', 'QsE', 'QtE',
#              'index', 'hand']
# drop_list = ['QaE', 'QbE', 'QcE', 'QdE', 'QeE',
#              'QfE', 'QgE', 'QhE', 'QiE', 'QjE',
#              'QkE', 'QlE', 'QmE', 'QnE', 'QoE',
#              'QpE', 'QqE', 'QrE', 'QsE', 'QtE',
#              'index']
drop_list = ['index']
replace_dict = {'education': str, 'engnat': str, 'married': str, 'urban': str}

In [4]:
import re

In [5]:
survey_time = []
for col in list(train_data.columns):
    if re.match('Q[a-z]E', col):
        survey_time.append(col)
train_data[survey_time] = train_data[survey_time].apply(lambda x: x / (x.max()*10), axis=1)   

survey_time = []
for col in list(test_data.columns):
    if re.match('Q[a-z]E', col):
        survey_time.append(col)
test_data[survey_time] = test_data[survey_time].apply(lambda x: x / (x.max()*10), axis=1)   

In [6]:
train_data.head()

index  QaA       QaE  QbA       QbE  QcA       QcE  QdA       QdE  QeA  \
0      0  3.0  0.023018  4.0  0.086874  5.0  0.063221  1.0  0.064933  2.0   
1      1  5.0  0.014946  5.0  0.030330  3.0  0.078240  5.0  0.068584  1.0   
2      2  4.0  0.048103  1.0  0.043865  1.0  0.030261  4.0  0.100000  5.0   
3      3  3.0  0.002112  3.0  0.009682  4.0  0.004156  3.0  0.013596  1.0   
4      4  1.0  0.049074  1.0  0.037427  5.0  0.029434  2.0  0.056220  1.0   

   ...  wr_04  wr_05  wr_06  wr_07  wr_08  wr_09  wr_10  wr_11  wr_12  wr_13  
0  ...      0      1      0      1      1      0      1      0      1      1  
1  ...      1      1      0      1      1      0      1      0      1      1  
2  ...      1      1      0      1      1      1      1      0      1      1  
3  ...      0      0      0      0      1      0      1      0      1      1  
4  ...      1      1      1      1      1      0      1      1      1      1  

[5 rows x 78 columns]

In [7]:
train_y = train_data['voted']
train_y = 2 - train_y.to_numpy()

train_x = train_data.drop(drop_list + ['voted'], axis=1)
train_x = train_x.astype(replace_dict)
train_x = pd.get_dummies(train_x)

test_x = test_data.drop(drop_list, axis=1)
test_x = test_x.astype(replace_dict)
test_x = pd.get_dummies(test_x)


In [8]:
for i, d in enumerate(train_x.columns):
    print(i, d)

0 QaA
1 QaE
2 QbA
3 QbE
4 QcA
5 QcE
6 QdA
7 QdE
8 QeA
9 QeE
10 QfA
11 QfE
12 QgA
13 QgE
14 QhA
15 QhE
16 QiA
17 QiE
18 QjA
19 QjE
20 QkA
21 QkE
22 QlA
23 QlE
24 QmA
25 QmE
26 QnA
27 QnE
28 QoA
29 QoE
30 QpA
31 QpE
32 QqA
33 QqE
34 QrA
35 QrE
36 QsA
37 QsE
38 QtA
39 QtE
40 familysize
41 hand
42 tp01
43 tp02
44 tp03
45 tp04
46 tp05
47 tp06
48 tp07
49 tp08
50 tp09
51 tp10
52 wf_01
53 wf_02
54 wf_03
55 wr_01
56 wr_02
57 wr_03
58 wr_04
59 wr_05
60 wr_06
61 wr_07
62 wr_08
63 wr_09
64 wr_10
65 wr_11
66 wr_12
67 wr_13
68 age_group_+70s
69 age_group_10s
70 age_group_20s
71 age_group_30s
72 age_group_40s
73 age_group_50s
74 age_group_60s
75 education_0
76 education_1
77 education_2
78 education_3
79 education_4
80 engnat_0
81 engnat_1
82 engnat_2
83 gender_Female
84 gender_Male
85 married_0
86 married_1
87 married_2
88 married_3
89 race_Arab
90 race_Asian
91 race_Black
92 race_Indigenous Australian
93 race_Native American
94 race_Other
95 race_White
96 religion_Agnostic
97 religion_Atheist
98 re

In [9]:
train_x = train_x.to_numpy()
test_x = test_x.to_numpy()

In [10]:
train_x[:, :40] = (train_x[:, :40] - 1.) / 4.
test_x[:, 40] = (test_x[:, 40] - 1.) / 4.

train_x[:, 41] = (train_x[:, 41]) / 3
test_x[:, 41] = (test_x[:, 41]) / 3

train_x[:, 42:52] = (train_x[:, 42:52] - 3.5) / 3.5
test_x[:, 42:52] = (test_x[:, 42:52] - 3.5) / 3.5

In [11]:
# train_x[:, :20] = (train_x[:, :20] - 1.) / 4.
# test_x[:, 20] = (test_x[:, 20] - 1.) / 4.

# train_x[:, 21] = (train_x[:, 21]) / 3
# test_x[:, 21] = (test_x[:, 21]) / 3

# train_x[:, 22:32] = (train_x[:, 22:32] - 3.5) / 3.5
# test_x[:, 22:32] = (test_x[:, 22:32] - 3.5) / 3.5

In [12]:
# train_x[:, :20] = (train_x[:, :20] - 3.) / 2.
# test_x[:, :20] = (test_x[:, :20] - 3.) / 2
# train_x[:, 20] = (train_x[:, 20] - 5.) / 5.
# test_x[:, 20] = (test_x[:, 20] - 5.) / 5.
# train_x[:, 21:31] = (train_x[:, 21:31] - 3.5) / 3.5
# test_x[:, 21:31] = (test_x[:, 21:31] - 3.5) / 3.5

In [13]:
train_x

array([[ 0.5       , -0.2442454 ,  0.75      , ...,  1.        ,
         0.        ,  0.        ],
       [ 1.        , -0.24626357,  1.        , ...,  0.        ,
         0.        ,  1.        ],
       [ 0.75      , -0.23797421,  0.        , ...,  0.        ,
         1.        ,  0.        ],
       ...,
       [ 0.75      , -0.24328882,  0.        , ...,  0.        ,
         1.        ,  0.        ],
       [ 0.        , -0.2455323 ,  0.5       , ...,  0.        ,
         0.        ,  0.        ],
       [ 0.5       , -0.2482476 ,  1.        , ...,  0.        ,
         1.        ,  0.        ]])

In [14]:
train_x = torch.from_numpy(train_x).float()
train_y = torch.from_numpy(train_y).float()

real_train_x = train_x
real_train_y = train_y

In [15]:
ratios = [.7, .3]

train_cnt = int(train_x.size(0) * ratios[0])
valid_cnt = train_x.size(0) - train_cnt
cnts = [train_cnt, valid_cnt]
train_cnt, valid_cnt

(31870, 13660)

In [16]:
indices = torch.randperm(train_x.size(0))

train_x = torch.index_select(train_x, dim=0, index=indices)
train_y = torch.index_select(train_y, dim=0, index=indices)

train_x = train_x.split(cnts, dim=0)
train_y = train_y.split(cnts, dim=0)

test_x = torch.tensor(test_x, dtype=torch.float32, device=DEVICE)

for x_i, y_i in zip(train_x, train_y):
    print(x_i.size(), y_i.size())

torch.Size([31870, 112]) torch.Size([31870])
torch.Size([13660, 112]) torch.Size([13660])


In [17]:
real_train_x.shape

torch.Size([45530, 112])

In [18]:
from copy import deepcopy

lowest_loss = np.inf
best_model = None
lowest_epoch = np.inf

In [22]:
train_len, test_len = len(train_x), len(test_x)
early_stop = 30
print_interval = 5
N_MODEL = 5
N_EPOCH = 100
BATCH_SIZE = 128
LOADER_PARAM = {
    'batch_size': BATCH_SIZE,
    'num_workers': 0,
    'pin_memory': False
}
prediction_valid = np.zeros((13660, 1), dtype=np.float32)
prediction_test = np.zeros((11383, 1), dtype=np.float32)

with torch.cuda.device(0):
    for no in range(N_MODEL):

        real_train_loader = DataLoader(TensorDataset(real_train_x, real_train_y),
                                  shuffle=True, drop_last=True, **LOADER_PARAM)
    
        train_loader = DataLoader(TensorDataset(train_x[0], train_y[0]),
                                  shuffle=True, drop_last=True, **LOADER_PARAM)
        valid_loader = DataLoader(TensorDataset(train_x[1], train_y[1]),
                                  shuffle=False, drop_last=True, **LOADER_PARAM)
    
        test_loader = DataLoader(TensorDataset(test_x, torch.zeros((test_len,), dtype=torch.float32, device=DEVICE)),
                                 shuffle=False, drop_last=False, **LOADER_PARAM)
        model = nn.Sequential(
            nn.Dropout(0.05),
            nn.Linear(112, 120, bias=False),
            nn.LeakyReLU(0.05, inplace=True),
            nn.BatchNorm1d(120),
            
            nn.Dropout(0.05),
            nn.Linear(120, 100, bias=False),
            nn.LeakyReLU(0.05, inplace=True),
            nn.BatchNorm1d(100),
            
            nn.Dropout(0.05),
            nn.Linear(100, 80, bias=False),
            nn.LeakyReLU(0.05, inplace=True),
            nn.BatchNorm1d(80),
            
            nn.Dropout(0.05),
            nn.Linear(80, 60, bias=False),
            nn.LeakyReLU(0.05, inplace=True),
            nn.BatchNorm1d(60),
            
            nn.Dropout(0.5),
            nn.Linear(60, 30, bias=False),
            nn.ReLU(inplace=True),
            nn.BatchNorm1d(30),
            
            nn.Linear(30, 1)
        ).to(DEVICE)
        criterion = torch.nn.BCEWithLogitsLoss(pos_weight=torch.tensor([1.20665], device=DEVICE))
        optimizer = optim.AdamW(model.parameters(), lr=1e-3, weight_decay=4e-2)
        scheduler = optim.lr_scheduler.CosineAnnealingWarmRestarts(
            optimizer, T_0=N_EPOCH // 4, eta_min=1.2e-5)

        for epoch in range(N_EPOCH):
#         for epoch in tqdm(range(N_EPOCH), desc='{:02d}/{:02d}'.format(no + 1, N_MODEL)):
            train_loss, valid_loss = 0, 0
            y_hat = []
        
            model.train()
            for idx, (xx, yy) in enumerate(real_train_loader):
                optimizer.zero_grad()
                print(xx.size())
                xx, yy = xx.to(DEVICE), yy.to(DEVICE)
                pred = model(xx).squeeze()
                loss = criterion(pred, yy)
                loss.backward()
                optimizer.step()
                scheduler.step(epoch + idx / len(real_train_loader))
                train_loss += float(loss)
                
            model.eval()
            with torch.no_grad():
                valid_loss = 0
                for idx, (xx, yy) in enumerate(valid_loader):
                    xx, yy = xx.to(DEVICE), yy.to(DEVICE)
                    pred = model(xx).squeeze()
                    loss = criterion(pred, yy)

                    valid_loss += float(loss)
                    y_hat += [pred]

            valid_loss = valid_loss / len(valid_loader)
    #         valid_history += [valid_loss]

            if (epoch + 1) % print_interval == 0:
                print('Epoch %d: train loss=%.4e  valid_loss=%.4e  lowest_loss=%.4e' % (
                    epoch + 1,
                    train_loss,
                    valid_loss,
                    lowest_loss,
                ))

            if valid_loss <= lowest_loss:
                lowest_loss = valid_loss
                lowest_epoch = epoch

                best_model = deepcopy(model.state_dict())
            else:
                if early_stop > 0 and lowest_epoch + early_stop < epoch + 1:
                    print("There is no improvement during last %d epochs." % early_stop)
                    break

        print("The best validation loss from epoch %d: %.4e" % (lowest_epoch + 1, lowest_loss))
        model.load_state_dict(best_model)

        model.eval()
        with torch.no_grad():
            for idx, (xx, _) in enumerate(valid_loader):
                xx = xx.to(DEVICE)
                pred = (2. - torch.sigmoid(model(xx).detach().to('cpu'))).numpy()
                prediction_valid[BATCH_SIZE * idx:min(BATCH_SIZE * (idx + 1), len(prediction_valid)), :] += pred[:, :] / N_MODEL

df = pd.read_csv('./data/sample_submission.csv')
df.iloc[:, 1:] = prediction_valid
df.to_csv('./result/{}.csv'.format(datetime.now().strftime('%m%d-%H%M')), index=False)

torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size(

torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size(

torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size(

torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size(

torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size(

...

torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size(

torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size(

torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size(

torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size([128, 112])
torch.Size(

ValueError: cannot set using a multi-index selection indexer with a different length than the value

In [ ]:
from sklearn.metrics import roc_auc_score

In [ ]:
prediction_valid = 2 - prediction_valid
roc_auc_score(train_y[1], prediction_valid)

1. 0.7664986978004593
2. 0.7675935061471474  (설문조사답변 정규화 다르게..)
3. 0.7710123794060724  ~ 0.7738559380625569 (hand변수 포함 + 정규화)
4. 0.7657323921703704  (familysize 정규화) --> 제외!!
5. 0.7611448774735629 ~ 0.7618059057348474 (설문시간 포함+ 정규화)
6. 0.77171753378888 ~ 0.7727322346127534 (설문시간 포함+ 정규화 + layer늘림)
7. 0.7677365629016805 ~ 0.7741115155537603 (설문시간 포함+ 정규화 + layer더 늘림)
8. 0.7635808020457102 ~ 0.776610620093519 (설문시간 포함+ 정규화 + layer더 늘림 + batchnorm)
9. 0.7643981540072351 ~ 0.7708937758928313 (설문시간 포함+ 정규화 + layer더 늘림 + batchnorm + 설문마키아벨리) --> 제외!!